## Imports

In [1]:
#!pip install pymorphy2

In [2]:
#!pip install navec

In [3]:
import pandas as pd
import numpy as np
import nltk

from pymorphy2 import MorphAnalyzer
import re

from sklearn.metrics.pairwise import cosine_similarity, manhattan_distances, euclidean_distances

In [4]:
# Loading data for nltk
nltk.download('punkt')

[nltk_data] Downloading package punkt to C:\Users\Матвей
[nltk_data]     Иванов\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

## Data loading

In [5]:
data = pd.read_json('data/ixbt.json')

In [6]:
data.head()

title  \
0  Первый на рынке смартфон с новой 108-мегапиксе...   
1  Стоечные сетевые хранилища Qnap TS-873AeU пост...   
2  Китайский космический корабль «Тяньчжоу-2» сош...   
3  Зачем делать новый смартфон лучше старого? Sam...   
4  Ford и GM остановят производство на двух завод...   

                                            subtitle  \
0                            Он получит экран AMOLED   
1               Они рассчитаны на восемь накопителей   
2  Он использовался для доставки грузов на китайс...   
3                    Платформа Exynos 850 сохранится   
4  Мировая автомобильная промышленность испытывае...   

                                                 url              time  \
0  https://www.ixbt.com/news/2022/04/01/108-realm...  01.04.2022 23:18   
1  https://www.ixbt.com/news/2022/04/01/qnap-ts-8...  01.04.2022 21:21   
2  https://www.ixbt.com/news/2022/04/01/kitajskij...  01.04.2022 21:15   
3  https://www.ixbt.com/news/2022/04/01/samsung-g...  01.04.2022 21:15   
4  https://www.ixbt.com/news/2022/04/01/ford-i-gm...  01.04.2022 20:51   

                                                text        tags       sources  
0  Информации о смартфоне Realme 9 4G, который пе...    [Realme]  [Gizmochina]  
1  Компания Qnap Systems представила серию хранил...     [Qnap ]        [Qnap]  
2  Как пишет Интерфакс со ссылкой на Центральное ...          []   [Интерфакс]  
3  Компания Samsung готовит ещё один очень доступ...   [Samsung]   [GSM Arena]  
4  Компании Ford Motor и General Motors (GM) на с...  [Ford, GM]     [Reuters]

## Preprocessing

We should use nltk tokenization and pymorphy lemmatization, because they were used for training word vectors

In [7]:
# Tokenization
tokenized_sent = [nltk.tokenize.word_tokenize(sent) for sent in data.text[:20]]

In [8]:
tokenized_sent

[['Информации',
  'о',
  'смартфоне',
  'Realme',
  '9',
  '4G',
  ',',
  'который',
  'первым',
  'на',
  'рынке',
  'получит',
  'новый',
  'датчик',
  'Samsung',
  'ISOCELL',
  'HM6',
  ',',
  'становится',
  'всё',
  'больше',
  '.',
  'В',
  'частности',
  ',',
  'в',
  'Сети',
  'появились',
  'рекламные',
  'постеры',
  'новинки',
  '.',
  'Они',
  'раскрывают',
  'дизайн',
  'смартфона',
  ',',
  'цветовые',
  'варианты',
  ',',
  'а',
  'также',
  'некоторые',
  'параметры',
  '.',
  'К',
  'примеру',
  ',',
  'теперь',
  'мы',
  'знаем',
  ',',
  'что',
  'Realme',
  '9',
  '4G',
  'получит',
  '90-герцевый',
  'дисплей',
  'Super',
  'AMOLED',
  '.',
  'Диагональ',
  'не',
  'указана',
  ',',
  'а',
  'разрешение',
  'явно',
  'составит',
  'Full',
  'HD+',
  '.',
  'Что',
  'касается',
  'дизайна',
  ',',
  'новинка',
  'будет',
  'выполнена',
  'в',
  'актуальном',
  'стиле',
  'Realme',
  '.',
  'Согласно',
  'ранним',
  'данным',
  ',',
  'смартфон',
  'получит',
  '6',


In [9]:
data.text[0]

'Информации о смартфоне Realme 9 4G, который первым на рынке получит новый датчик Samsung ISOCELL HM6, становится всё больше. В частности, в Сети появились рекламные постеры новинки. Они раскрывают дизайн смартфона, цветовые варианты, а также некоторые параметры. К примеру, теперь мы знаем, что Realme 9 4G получит 90-герцевый дисплей Super AMOLED. Диагональ не указана, а разрешение явно составит Full HD+. Что касается дизайна, новинка будет выполнена в актуальном стиле Realme. Согласно ранним данным, смартфон получит 6 ГБ ОЗУ и аккумулятор ёмкостью 5000 мА•ч с 33-ваттной зарядкой.'

In [10]:
# Lemmatization and deleting stop words
morph = MorphAnalyzer()
rus_stop_words = nltk.corpus.stopwords.words('russian')

lemmatized_sent = [[morph.parse(word)[0].normal_form for word in item if re.match('[А-я]+', word) and word not in rus_stop_words]
                   for item in tokenized_sent]

In [11]:
lemmatized_sent

[['информация',
  'смартфон',
  'который',
  'первый',
  'рынок',
  'получить',
  'новый',
  'датчик',
  'становиться',
  'всё',
  'в',
  'частность',
  'сеть',
  'появиться',
  'рекламный',
  'постер',
  'новинка',
  'они',
  'раскрывать',
  'дизайн',
  'смартфон',
  'цветовой',
  'вариант',
  'также',
  'некоторый',
  'параметр',
  'к',
  'пример',
  'знать',
  'получить',
  'дисплей',
  'диагональ',
  'указать',
  'разрешение',
  'явно',
  'составить',
  'что',
  'касаться',
  'дизайн',
  'новинка',
  'выполнить',
  'актуальный',
  'стиль',
  'согласно',
  'ранний',
  'данные',
  'смартфон',
  'получить',
  'гб',
  'оз',
  'аккумулятор',
  'ма•ча',
  'зарядка'],
 ['компания',
  'представить',
  'серия',
  'хранилище',
  'сетевой',
  'подключение',
  'серия',
  'включать',
  'модель',
  'это',
  'форм-фактор',
  'малый',
  'глубина',
  'мм',
  'рассчитать',
  'монтаж',
  'стойка',
  'отличительный',
  'черта',
  'второй',
  'модель',
  'являться',
  'резервирование',
  'блок',
  'пит

In [12]:
%%time
# Creating vocabulary
all_words = list()
for sent in lemmatized_sent:
    all_words += sent
    
vocabulary = {word: 0 for word in set(all_words)}

Wall time: 998 µs


In [13]:
%%time
# Getting embedding vectors for our vocabulary
with open('data/ft_native_300_ru_wiki_lenta_lemmatize.vec', "rt", encoding="UTF-8") as file:
    counter = 0

    file.readline() # Reading first useless line
    for line in file:
        elements = line.split(' ')
        if elements[0] in vocabulary:
            vocabulary[elements[0]] = np.array(elements[1:-1], np.float16)

Wall time: 26.5 s


In [14]:
%%time
# Finding idf values for each word
idf_coefs = dict()
text_num = len(lemmatized_sent)

for sent in lemmatized_sent:
    unique_words = set(sent)
    for word in unique_words:
        idf_coefs[word] = (idf_coefs.get(word, 0) + 1) / text_num

Wall time: 978 µs


In [15]:
idf_coefs

{'раскрывать': 0.052500000000000005,
 'рынок': 0.052625,
 'первый': 0.05263157890625,
 'составить': 0.052625,
 'информация': 0.05,
 'постер': 0.05,
 'в': 0.052631578947265625,
 'некоторый': 0.05,
 'вариант': 0.052625,
 'выполнить': 0.05,
 'касаться': 0.052500000000000005,
 'оз': 0.05263125,
 'явно': 0.05,
 'новинка': 0.05263125,
 'указать': 0.05,
 'разрешение': 0.052500000000000005,
 'аккумулятор': 0.052631578125,
 'что': 0.052625,
 'они': 0.05,
 'ранний': 0.052500000000000005,
 'пример': 0.052500000000000005,
 'новый': 0.052631578125,
 'смартфон': 0.05263156249999999,
 'частность': 0.052500000000000005,
 'сеть': 0.052625,
 'параметр': 0.052500000000000005,
 'датчик': 0.052625,
 'к': 0.05263125,
 'дисплей': 0.052500000000000005,
 'всё': 0.052500000000000005,
 'знать': 0.05,
 'рекламный': 0.05,
 'согласно': 0.052625,
 'актуальный': 0.052500000000000005,
 'появиться': 0.052500000000000005,
 'становиться': 0.05,
 'зарядка': 0.052625,
 'получить': 0.052631578125,
 'ма•ча': 0.052625,
 'цвет

In [16]:
vocabulary

{'выступать': array([-2.3621e-01, -1.4319e-01,  1.9116e-01, -4.2725e-02, -7.0620e-04,
         4.2419e-02, -1.1194e-01, -5.7953e-02, -4.7363e-02,  2.3120e-01,
         8.8013e-02,  1.3123e-01, -1.5434e-02, -8.1970e-02,  3.3569e-01,
         1.3342e-01, -2.5415e-01, -2.1838e-01, -1.2817e-01,  2.2351e-01,
         2.1805e-02, -1.0590e-01,  1.7105e-02,  5.5847e-02, -1.5393e-01,
        -7.6599e-02,  3.0933e-01,  2.9736e-01, -4.3213e-01,  3.0835e-01,
        -7.6843e-02,  3.3716e-01, -1.3403e-01, -1.2646e-01,  7.7759e-02,
        -1.4099e-01, -2.1484e-01, -2.6733e-01,  2.7783e-01,  1.2134e-01,
        -1.6626e-01,  1.8323e-01,  2.3145e-01,  3.2275e-01,  8.6914e-02,
        -2.5146e-01, -1.3049e-01, -3.4961e-01,  1.4880e-01, -1.6455e-01,
         2.2217e-02,  1.1743e-01, -6.8787e-02,  1.2262e-01,  2.1545e-01,
         2.3083e-01,  2.2131e-01, -4.4495e-02,  2.9370e-01,  2.5830e-01,
        -2.2110e-02,  1.5283e-01,  3.5583e-02,  2.2522e-01, -2.7222e-01,
        -1.7227e-02,  2.3389e-01, -7.0

In [17]:
%%time
# Getting document vector
text_vectors = list()
doc_vect_size = vocabulary[list(vocabulary.keys())[0]].shape[0]

for text in lemmatized_sent:
    t_text_vector = np.zeros(doc_vect_size, dtype=np.float16)
    for word_id, word in enumerate(text):
        t_text_vector += vocabulary.get(word, 1) * idf_coefs.get(word, 0)
    t_text_vector /= word_id + 1
    
    text_vectors.append(t_text_vector)

Wall time: 25.9 ms


In [18]:
text_vectors

[array([-9.8267e-03, -1.3304e-04,  1.0536e-02,  6.8169e-03, -1.6155e-03,
         2.2564e-03, -2.0866e-03,  7.7868e-04,  8.9569e-03,  7.8430e-03,
        -3.9177e-03, -1.5793e-03, -4.0588e-03, -3.8719e-04, -9.1934e-03,
         3.5362e-03,  3.6025e-04, -7.2336e-04,  2.7323e-04, -4.7565e-04,
        -2.9545e-03,  1.3351e-02, -4.7226e-03, -9.3994e-03, -6.5231e-03,
        -1.2489e-02,  3.0785e-03,  5.2910e-03,  2.0599e-03,  1.7014e-03,
         1.7872e-03, -1.3247e-03,  1.0445e-02,  6.9466e-03,  7.9269e-03,
        -1.7185e-03,  5.7507e-04, -4.2114e-03, -7.8249e-04, -3.2635e-03,
         7.0496e-03,  1.4467e-03,  1.5802e-03, -3.0918e-03,  2.4395e-03,
        -8.7357e-03, -1.4601e-03, -6.9046e-03,  1.8988e-03, -1.0017e-02,
         1.2787e-02,  7.6523e-03, -2.5711e-03, -4.3640e-03,  5.0468e-03,
        -1.0967e-03,  1.1398e-02, -4.1237e-03,  1.0513e-02,  9.7609e-04,
        -4.4365e-03,  7.1678e-03, -3.2749e-03, -2.3041e-03, -6.6795e-03,
         4.3449e-03,  1.1589e-02, -6.6471e-04,  6.5

## Model pipeline

In [19]:
def top_similar_vectors(text_vectors: list, target_vector: np.array, max_count: int):
    target_vector = target_vector.reshape((1, -1))
    
    vectors_dist = [{'text_id': text_id, 
                     'Cosine measure': cosine_similarity(t_vect.reshape((1, -1)), target_vector)[0][0],
                     'Manhattan distance': manhattan_distances(t_vect.reshape((1, -1)), target_vector)[0][0],
                     'Euclidian distance': euclidean_distances(t_vect.reshape((1, -1)), target_vector)[0][0],
                    } 
                    for text_id, t_vect in enumerate(text_vectors)]
    return sorted(vectors_dist, key=lambda x: x['Cosine measure'], reverse=True)[:max_count]

In [20]:
def check_similarity(text_vectors: list):
    syn_cosine_similarities_dct = dict()
    text_embed_with_syn = text_vectors

    for i in range(len(text_embed_with_syn)):
        for j in range(i + 1, len(text_embed_with_syn)):
            first_vector = text_embed_with_syn[i].reshape(1, -1)
            second_vector = text_embed_with_syn[j].reshape(1, -1)
            syn_cosine_similarities_dct[f'{i} - {j}'] = {
                "Cosine measure": cosine_similarity(first_vector, second_vector)[0][0],
                "Manhattan distance": manhattan_distances(first_vector, second_vector)[0][0],
                "Euclidian distance": euclidean_distances(first_vector, second_vector)[0][0],
            }
            
    for pair, similarity in sorted(syn_cosine_similarities_dct.items(), key=lambda x: x[1]["Cosine measure"], reverse=True):
        print(f"Pair {pair} -> {similarity}")

In [21]:
class SimilarityModel:
    def __init__(self, vect_path: str):
        self.tokenizer = nltk.tokenize.word_tokenize
        self.morph_analyzer = MorphAnalyzer()
        self.stop_words_lst = nltk.corpus.stopwords.words('russian')
        self.word_regex = '[А-я]+'
        self.vocabulary = dict()
        self.idf_coefs = dict()
        self.vect_path = vect_path
        self.vec_size = 0
    
    def train(self, texts: list):
        preprocessed_texts = self.__preprocessing__(texts)
        
        # Creating vocabulary
        all_words = list()
        for t_text in preprocessed_texts:
            all_words += t_text

        self.vocabulary = {word: 1 for word in set(all_words)}
        
        # Getting embedding vectors for our vocabulary
        with open(self.vect_path, "rt", encoding="UTF-8") as file:
            file.readline() # Reading first useless line
            for line in file:
                elements = line.split(' ')
                if elements[0] in self.vocabulary:
                    self.vocabulary[elements[0]] = np.array(elements[1:-1], np.float16)
        
        # Finding idf values for each word
        text_num = len(preprocessed_texts)

        for t_text in preprocessed_texts:
            unique_words = set(t_text)
            for word in unique_words:
                self.idf_coefs[word] = (idf_coefs.get(word, 0) + 1) / text_num
        # Saving word vector size
        self.vec_size = self.vocabulary[list(self.vocabulary.keys())[0]].shape[0]
                
    def get_text_vect(self, text: str):
        # Getting document vector
        text_vector = np.zeros(self.vec_size, dtype=np.float16)
        
        # Text preprocessing
        prep_text = self.__preprocessing__([text])[0]
        
        for word_id, word in enumerate(prep_text):
            text_vector += self.vocabulary.get(word, 1) * self.idf_coefs.get(word, 0)
        text_vector /= word_id + 1
        
        return text_vector

        
    def __preprocessing__(self, texts: list):
        # Tokenization
        tokenized_texts = [self.tokenizer(t_text) for t_text in texts]
        
        # Lemmatization
        lemm_texts = [[self.morph_analyzer.parse(word)[0].normal_form for word in t_text 
                       if re.match(self.word_regex, word)] for t_text in tokenized_texts]
        
        # Deleting stop words
        preprocessed_texts = [[word for word in t_text if word not in self.stop_words_lst] for t_text in lemm_texts]
        
        return preprocessed_texts

In [22]:
%%time
model = SimilarityModel('data/ft_native_300_ru_wiki_lenta_lemmatize.vec')

model.train(data.text[:40])

Wall time: 28 s


In [23]:
syntatic_text = "Samsung готовит ещё один очень бюджетный смартфон. Galaxy F13 уже засветился в Geekbench, что" +\
"позволяет нам заодно узнать его основные параметры. "       +\
"При тестах платформа набирает 157 и 587 баллов в однопоточном и многопоточном режимах соответственно. При этом у " +\
"этого тестового аппарата было 4 ГБ оперативной памяти. Например Galaxy F12 "        +\
"основан на той же платформе и имеет тот же объём памяти. То есть с точки зрения производительности разницы не будет "        +\
"вообще никакой. Если теория подтвердится и Galaxy F13 будет копией Galaxy A13, то экран увеличится, а ёмкость аккумулятора снизится."

In [24]:
%%time
text_vectors = [model.get_text_vect(t_text) for t_text in data.text[:40]]
target_vector = model.get_text_vect(syntatic_text)

Wall time: 2.16 s


In [25]:
%%time
check_similarity(text_vectors + [target_vector])

Pair 3 - 40 -> {'Cosine measure': 0.969918966004929, 'Manhattan distance': 0.17962205410003662, 'Euclidian distance': 0.012815220496009134}
Pair 17 - 34 -> {'Cosine measure': 0.9548800153063883, 'Manhattan distance': 0.2244141697883606, 'Euclidian distance': 0.01656904185751298}
Pair 0 - 17 -> {'Cosine measure': 0.9548034847830171, 'Manhattan distance': 0.22596663236618042, 'Euclidian distance': 0.016492173682771467}
Pair 3 - 29 -> {'Cosine measure': 0.9535083976871319, 'Manhattan distance': 0.21561962366104126, 'Euclidian distance': 0.015501501186093768}
Pair 3 - 19 -> {'Cosine measure': 0.9507256716385095, 'Manhattan distance': 0.22851449251174927, 'Euclidian distance': 0.01627428251140929}
Pair 0 - 34 -> {'Cosine measure': 0.9452363847612565, 'Manhattan distance': 0.24825918674468994, 'Euclidian distance': 0.017625755035639717}
Pair 17 - 19 -> {'Cosine measure': 0.9450659550610565, 'Manhattan distance': 0.25473862886428833, 'Euclidian distance': 0.01809328745429806}
Pair 6 - 12 -> {

In [26]:
print("Text #17")
print(data.text[0])
print()
print("Text #34")
print(data.text[17])

Text #17
Информации о смартфоне Realme 9 4G, который первым на рынке получит новый датчик Samsung ISOCELL HM6, становится всё больше. В частности, в Сети появились рекламные постеры новинки. Они раскрывают дизайн смартфона, цветовые варианты, а также некоторые параметры. К примеру, теперь мы знаем, что Realme 9 4G получит 90-герцевый дисплей Super AMOLED. Диагональ не указана, а разрешение явно составит Full HD+. Что касается дизайна, новинка будет выполнена в актуальном стиле Realme. Согласно ранним данным, смартфон получит 6 ГБ ОЗУ и аккумулятор ёмкостью 5000 мА•ч с 33-ваттной зарядкой.

Text #34
Компания Lenovo готовится пополнить ассортимент смартфонов Motorola моделью Moto G62. Когда случится официальная премьера — данных нет, но источник уже опубликовал качественный рендер смартфона и перечень предполагаемых характеристик. С аппаратной точки зрения Moto G62 станет конкурентом Redmi Note 11 Pro 5G: новинке приписана та же SoC Snapdragon 695 5G. Ожидается, что Moto G62 также получи

In [27]:
top_similar_vectors(text_vectors, target_vector, max_count=5)

[{'text_id': 3,
  'Cosine measure': 0.969918966004929,
  'Manhattan distance': 0.17962205410003662,
  'Euclidian distance': 0.012815220496009134},
 {'text_id': 29,
  'Cosine measure': 0.9371461522782942,
  'Manhattan distance': 0.2406279444694519,
  'Euclidian distance': 0.017361845288003636},
 {'text_id': 36,
  'Cosine measure': 0.9312623474938352,
  'Manhattan distance': 0.2547789216041565,
  'Euclidian distance': 0.01858706421018075},
 {'text_id': 1,
  'Cosine measure': 0.9270086303441752,
  'Manhattan distance': 0.2945897579193115,
  'Euclidian distance': 0.021729189379674555},
 {'text_id': 19,
  'Cosine measure': 0.9123399616826898,
  'Manhattan distance': 0.30298298597335815,
  'Euclidian distance': 0.021372829826981684}]

## Navec embeddings

In [28]:
from navec import Navec

path = 'data/navec_news_v1_1B_250K_300d_100q.tar'
vocabulary = Navec.load(path)

In [29]:
model.vocabulary = vocabulary

In [30]:
%%time
text_vectors = [model.get_text_vect(t_text) for t_text in data.text[:40]]
text_vectors.append(model.get_text_vect(syntatic_text))

Wall time: 2.5 s


In [31]:
%%time
check_similarity(text_vectors)

Pair 18 - 26 -> {'Cosine measure': 0.9392818208704197, 'Manhattan distance': 0.337992787361145, 'Euclidian distance': 0.024340983601996862}
Pair 3 - 40 -> {'Cosine measure': 0.9332450245166481, 'Manhattan distance': 0.2902064919471741, 'Euclidian distance': 0.020713219026351523}
Pair 17 - 34 -> {'Cosine measure': 0.9232232289701254, 'Manhattan distance': 0.3490874171257019, 'Euclidian distance': 0.025836958679511527}
Pair 11 - 18 -> {'Cosine measure': 0.9230092628372941, 'Manhattan distance': 0.35653871297836304, 'Euclidian distance': 0.025907003222009256}
Pair 26 - 34 -> {'Cosine measure': 0.9221582482879764, 'Manhattan distance': 0.3801855444908142, 'Euclidian distance': 0.027488822218991203}
Pair 11 - 26 -> {'Cosine measure': 0.9164848669128733, 'Manhattan distance': 0.4009167551994324, 'Euclidian distance': 0.02844419988964664}
Pair 19 - 29 -> {'Cosine measure': 0.9159032142376957, 'Manhattan distance': 0.34033203125, 'Euclidian distance': 0.023736886946594784}
Pair 0 - 34 -> {'Cos

In [32]:
%%time
orig_vect = [model.get_text_vect(t_text) for t_text in data.text[:40]]
target_vect = model.get_text_vect(syntatic_text)

Wall time: 2.19 s


In [33]:
similar_texts = top_similar_vectors(orig_vect, target_vect, 10)

In [34]:
for text in similar_texts:
    print(f"Text #{text['text_id']} -> Cosine measure = {round(text['Cosine measure'], 4)}, " + \
          f"Manh Dist = {round(text['Manhattan distance'], 4)}, " + \
          f"Eucl Dist = {round(text['Euclidian distance'], 4)}")

Text #3 -> Cosine measure = 0.9332, Manh Dist = 0.2902, Eucl Dist = 0.0207
Text #19 -> Cosine measure = 0.8963, Manh Dist = 0.3594, Eucl Dist = 0.0261
Text #29 -> Cosine measure = 0.8875, Manh Dist = 0.3517, Eucl Dist = 0.0252
Text #36 -> Cosine measure = 0.8678, Manh Dist = 0.3929, Eucl Dist = 0.0281
Text #18 -> Cosine measure = 0.8537, Manh Dist = 0.4881, Eucl Dist = 0.0352
Text #34 -> Cosine measure = 0.8423, Manh Dist = 0.4919, Eucl Dist = 0.0363
Text #26 -> Cosine measure = 0.8372, Manh Dist = 0.5216, Eucl Dist = 0.0391
Text #17 -> Cosine measure = 0.8353, Manh Dist = 0.4741, Eucl Dist = 0.034
Text #0 -> Cosine measure = 0.83, Manh Dist = 0.4728, Eucl Dist = 0.0342
Text #23 -> Cosine measure = 0.8292, Manh Dist = 0.4531, Eucl Dist = 0.0324


## Fact checking
We should check facts from incoming article with the original one

In [35]:
data.text[3]

'Компания Samsung готовит ещё один очень доступный смартфон. Galaxy F13 уже засветился в Geekbench, что позволяет нам заодно узнать его основные параметры. В частности, сердцем новинки послужит SoC Exynos 850 — самая простая и бюджетная однокристальная система Samsung среди актуальных. Напомним, в её конфигурацию входят восемь ядер Cortex-A55 с частотой 2 ГГц и GPU Mali-G52 MP1. В бенчмарке платформа набирает 157 и 587 баллов в однопоточном и многопоточном режимах соответственно. При этом у тестового аппарата было 4 ГБ ОЗУ. Для сравнения, Galaxy F12 основан на той же платформе и имеет те же 4 ГБ ОЗУ. То есть с точки зрения производительности разницы не будет вообще никакой. Что изменится, неясно. Если слухи верны, и Galaxy F13 будет копией Galaxy A13, то экран увеличится до 6,6 дюйма, а ёмкость аккумулятора снизится до 5000 мА•ч.'

In [36]:
syntatic_text

'Samsung готовит ещё один очень бюджетный смартфон. Galaxy F13 уже засветился в Geekbench, чтопозволяет нам заодно узнать его основные параметры. При тестах платформа набирает 157 и 587 баллов в однопоточном и многопоточном режимах соответственно. При этом у этого тестового аппарата было 4 ГБ оперативной памяти. Например Galaxy F12 основан на той же платформе и имеет тот же объём памяти. То есть с точки зрения производительности разницы не будет вообще никакой. Если теория подтвердится и Galaxy F13 будет копией Galaxy A13, то экран увеличится, а ёмкость аккумулятора снизится.'

### Tasks:
* Check dates?
* Check numerical values
* Check names(cities, companyes, models and other)

### Numerical values

In [37]:
import re

In [38]:
# Preparing values
original_text = data.text[3]
target_text = syntatic_text

In [39]:
# Extraction numerical values
pattern = r"\b((\d+[.,]\d+)|(\d+))\b"
original_values = re.findall(pattern, original_text)
target_values = re.findall(pattern, target_text)

In [40]:
def check_num_values(original_text: str, target_text: str):
    pattern = r"\b((\d+[.,]\d+)|(\d+))\b"
    original_values = re.findall(pattern, original_text)
    target_values = re.findall(pattern, target_text)
    
    results = {
        'recall': 0,
        'right_values': list(),
        'unknown_values': list(),
    }
    
    right_values = 0
    
    for item in target_values:
        if item in original_values:
            right_values += 1
            results['right_values'].append(item)
            del original_values[original_values.index(item)]
        else:
            results['unknown_values'].append(item)
    
    print(original_values)
    print(len(original_values))
    results['recall'] = right_values / len(original_values) if len(original_values) != 0 else 1
    
    return results

In [41]:
original_values

[('850', '', '850'),
 ('2', '', '2'),
 ('157', '', '157'),
 ('587', '', '587'),
 ('4', '', '4'),
 ('4', '', '4'),
 ('6,6', '6,6', ''),
 ('5000', '', '5000')]

In [42]:
target_values

[('157', '', '157'), ('587', '', '587'), ('4', '', '4')]

In [43]:
sum([1 for i in target_values if i in original_values]) / len(target_values)

1.0

### Names

In [44]:
# Extraction numerical values
eng_pattern = r"[A-Z][A-z\d\-]+"
rus_pattern = r"[А-Я][А-я\d\-]+"

original_names = [item for item in re.findall(eng_pattern, original_text)] + \
                 [item for item in re.findall(rus_pattern, original_text) 
                  if model.morph_analyzer.parse(item)[0].normal_form not in model.vocabulary]

target_names = [item for item in re.findall(eng_pattern, target_text)] + \
               [item for item in re.findall(rus_pattern, target_text) 
                if model.morph_analyzer.parse(item)[0].normal_form not in model.vocabulary]

In [45]:
def check_names(original_text: str, target_text: str):
    eng_pattern = r"[A-Z][A-z\d\-]+"
    rus_pattern = r"[А-Я][А-я\d\-]+"

    original_names = [item for item in re.findall(eng_pattern, original_text)] + \
                     [item for item in re.findall(rus_pattern, original_text) 
                      if model.morph_analyzer.parse(item)[0].normal_form not in model.vocabulary]

    target_names = [item for item in re.findall(eng_pattern, target_text)] + \
                   [item for item in re.findall(rus_pattern, target_text) 
                    if model.morph_analyzer.parse(item)[0].normal_form not in model.vocabulary]
    
    results = {
        'recall': 0,
        'right_names': list(),
        'unknown_names': list(),
    }
    
    right_values = 0
    
    for item in target_names:
        if item in original_names:
            right_values += 1
            results['right_names'].append(item)
            del original_names[original_names.index(item)]
        else:
            results['unknown_names'].append(item)
           
    results['recall'] = right_values / (len(original_names) + len(target_names)) if len(original_names) + len(target_names) != 0 else 1
    
    return results

In [46]:
original_names

['Samsung',
 'Galaxy',
 'F13',
 'Geekbench',
 'SoC',
 'Exynos',
 'Samsung',
 'Cortex-A55',
 'GPU',
 'Mali-G52',
 'MP1',
 'Galaxy',
 'F12',
 'Galaxy',
 'F13',
 'Galaxy',
 'A13']

In [47]:
target_names

['Samsung',
 'Galaxy',
 'F13',
 'Geekbench',
 'Galaxy',
 'F12',
 'Galaxy',
 'F13',
 'Galaxy',
 'A13']

In [48]:
sum([1 for i in target_names if i in original_names]) / len(target_names)

1.0

## Testing

Let's use all our dataset

In [49]:
data.shape

(4044, 7)

In [50]:
%%time
# Time when we are using Pavlovs vectors
model.train(data.text)

Wall time: 4min 35s


In [51]:
np.random.seed(3010)

random_texts_id = np.random.choice(np.arange(0, data.shape[0]), size=5)

In [52]:
random_texts = data.text[random_texts_id]

In [53]:
for text_id, text in zip(random_texts_id, random_texts):
    print(f"Text #{text_id}")
    print(text)
    print()

Text #83
Оперативная память DDR3 вскоре начнёт постепенно исчезать с рынка. Samsung уведомила клиентов о том, что будет принимать заказы на такую память до конца текущего года, а завершить выполнение всех заказов намерена до конца следующего. Hynix также ждёт прекращения производства DDR3, хотя относительно планов этой компании точных данных нет. А вот Micron пока не планирует прекращать производство, но это не означает, что компания будет выпускать DDR3 ещё много лет. Несмотря на то, что компьютеры и смартфоны уже давно перешли на DDR4, а сейчас переходят на DDR5, память DDR3 остаётся востребованной. Она используется в менее требовательных к производительности устройствах, да и для ремонта запасы нужны будут ещё достаточно долго.

Text #853
В Сети опубликованы качественные рендеры перспективного смартфона OnePlus Ace среднего уровня, а также его живые фото, видеотизер и довольно подробный перечень характеристик. Официальная премьера его состоится 21 апреля, но уже можно оценить и диза

In [54]:
new_texts = [
    #83 (Slight)
    "Оперативная память DDR3 вскоре начнёт постепенно исчезать с рынка. Одна известная компания уведомила клиентов о том," + \
    " что будет принимать заказы на такую память до конца текущего года, а завершить выполнение всех заказов" + \
    " намерена до конца следующего. Hynix также ждёт прекращения производства DDR3." + \
    " А вот Micron пока не планирует прекращать создание такой памяти, но это не " + \
    "означает, что компания будет выпускать DDR3 ещё много лет. Несмотря на то, что компьютеры и смартфоны" + \
    " уже давно перешли на DDR4, а сейчас переходят на DDR5, старая память остаётся востребованной. Она используется" + \
    " в менее требовательных к производительности устройствах, да и для ремонта запасы нужны будут ещё достаточно долго.",
    #853 (Medium -> less text and synonims)
    "В Сети опубликованы качественные снимки перспективного смартфона OnePlus Ace среднего уровня." + \
    " Официальная премьера его" + \
    " состоится 21 апреля, но уже можно оценить и внешний вид, и спецификации. OnePlus Ace похож на Realme GT" + \
    " Neo 3, но есть и отличительная особенность в виде полосок, которые визуально делят" + \
    " крышку надвое." + \
    " В основе аппаратной" + \
    " системы — SoC MediaTek Dimensity 8100. Ace станет первой моделью OnePlus с фронтальной камерой," + \
    " врезанной по центру экрана. Основная камера — с датчиками" + \
    " разрешением 50 Мп (Sony IMX766, с оптической стабилизацией), 8 и 2 Мп. Также будет аккумулятор" + \
    " ёмкостью 4500 мА·ч с поддержкой быстрой зарядки мощностью 150 Вт." + \
    " OnePlus Ace приписаны две конфигурации памяти: 8/128 ГБ и 12/256 ГБ. Цен пока нет",
    #2326 (Medium -> more text and synonims)
    "Замминистра цифрового развития России Дмитрий Ким подтвердил, что пользователи мобильных телефонов из Донецкой" + \
    " и Луганской народных республик (ДНР и ЛНР) получили российские номера с префиксом «+7». С 7 мая" + \
    " абоненты ДНР и ЛНР автоматически перешли с «украинских» префиксов «+38071» и «+38072». При совершении" + \
    " звонков и отправке смсок их номера телефонов будут отображаться как российские, с префиксами" + \
    " «+7(949)» и «+7(959)» соответственно. Замена кодовой нумерации абонентов ДНР и ЛНР на вызовах в Россию" + \
    " является шагом к упрощению жизни людей проживающих на этих территориях." + \
    "Огромное кол-во людей считают эту инициативу очень полезной и нужной, и хотят, чтобы сотрудничество продолжалось."
    " Такая кодовая нумерация для жителей данных территорий является логичным" + \
    " продолжением реализации подписанных ранее договоров [о сотрудничестве между республиками и Россией." + \
    " Дмитрий Ким Министр связи ДНР добавил, что можно «осуществлять звонки не только на территории республики," + \
    " но и за ее пределы». Министр связи ЛНР заявил, что это «прорыв связной блокады» и данный шаг поможет нашим народам стать ближе.",
    #2958 (Hard -> changed text and fakes)
    "Новый кроссовер Chery Tiggo 10 Pro поступил в продажу в Китае, но эта машина очень сильно отличается от российской" + \
    " версии — в РФ под названием Chery Tiggo 10 Pro вышел китайский автомобиль Tiggo 8 Plus, который продолжает продаваться" + \
    " в регионе. "+ \
    "Спрос на него неизменно растёт, хотя в свете последних событий всё может поменяться." + \
    "Всем потенциальным покупателям доступны 10 различных комплектаций Chery Tiggo 10 Pro с индексом 290Т, который" + \
    " предлагается по выгодной цене. Этот автомобиль комплектуется 1,6-литровым" + \
    " турбированным двигателем SQRF4J16 мощностью 197 л.с. с 290 Нм крутящего момента, огромным снэкбаром, а также только с передним" + \
    " приводом." + \
    " Хотя если хорошо попросить наших китайских коллег, то всё может измениться для вас)."
    " Кроме того, в продаже есть ещё вариант с индексом 390ТE. Цены переднеприводных Chery Tiggo 10 Pro" + \
    " варьируются от 1,36 до 1,46 млн рублей. Полноприводный вариант кроссовера доступен по цене от 3" + \
    " млн рублей. Все версии с индексом 390Т будут оснащаться 2-литровым турбодвигателем SQRF4J20. Он имеет мощность" + \
    " 300 л.с. и 520 Нм крутящего момента. Все новые версии Tiggo 10 Pro комплектуются 12-ступенчатой роботизированной" + \
    " трансмиссией Getrag с двойным «мокрым» сцеплением, а также доской для скейта. Также покупателю доступен выбор между 5- или 7-местным" + \
    " вариантами салона. Позже в продаже должна появиться гибридная версия кроссовера под названием Tiggo 12 Pro" + \
    " Kunpeng e+ DHT (PHEV).",
    #3921 (Hard -> changed text and fakes)
    "Компания Ford объявила о рекордном снижении цен почти на все свои автомобили, но теперь можно продавать машины конкурентов," + \
    "которые продаются в России после мартовского" + \
    " подорожания. Смотря какую модель выбрать, то их цены снизились на сумму от 720 тыс. до 3,45 млн рублей. Ford Focus 2.0" + \
    " Coupe подешевели до смешных копеек, самые большие скидки объявлены на автомобили серии BMW M8, не имею понятия почему именно эта марка," + \
    " которые теперь" + \
    " стоят от 20 мультов рублей. Хотя курса рубля и укрепился, но дефицит автомобилей в России позволяет дилерам" + \
    " не торопиться со снижением цен, поэтому желающие срочно купить автомобиль делают это по завышенным ценам. Новые" + \
    " на автомобили BMW в России, в скобках указано изменение:",
]

In [55]:
%%time
all_data_vectors = [model.get_text_vect(item) for item in data.text]

Wall time: 4min 14s


In [56]:
%%time
new_texts_vectors = [model.get_text_vect(item) for item in new_texts]

Wall time: 307 ms


In [57]:
%%time
counter = 0
for text_id, item in zip(random_texts_id, new_texts_vectors):
    print("---------------------------------------")
    print(f"Text #{text_id}:")
    %time sim_vect_res = top_similar_vectors(all_data_vectors, item, 5)
    print(sim_vect_res)
    %time print(check_names(data.text[sim_vect_res[0]['text_id']], new_texts[counter]))
    %time print(check_num_values(data.text[sim_vect_res[0]['text_id']], new_texts[counter]))
    counter += 1

---------------------------------------
Text #83:
Wall time: 2.31 s
[{'text_id': 83, 'Cosine measure': 0.9951145435391039, 'Manhattan distance': 0.0006177425384521484, 'Euclidian distance': 4.513240716918999e-05}, {'text_id': 3056, 'Cosine measure': 0.9331955112903582, 'Manhattan distance': 0.0022638440132141113, 'Euclidian distance': 0.00016421761126491708}, {'text_id': 43, 'Cosine measure': 0.9290260847784382, 'Manhattan distance': 0.0024712085723876953, 'Euclidian distance': 0.00017666114874913364}, {'text_id': 338, 'Cosine measure': 0.9277787148431864, 'Manhattan distance': 0.0024690628051757812, 'Euclidian distance': 0.00017675055675392588}, {'text_id': 424, 'Cosine measure': 0.9271920929620758, 'Manhattan distance': 0.002380669116973877, 'Euclidian distance': 0.0001731970984695048}]
{'recall': 0.7272727272727273, 'right_names': ['DDR3', 'Hynix', 'DDR3', 'Micron', 'DDR3', 'DDR4', 'DDR5', 'Она'], 'unknown_names': ['Одна']}
Wall time: 1 ms
[]
0
{'recall': 1, 'right_values': [], 'unk

In [58]:
abstract_text = "Привет мир, насколько эффективно можно использовать современные " + \
"технологии искусственного интеллекта и машинного обучения? Сегодня, думаю, мы с этим разберёмся"

In [59]:
%%time
abstr_vect = model.get_text_vect(abstract_text)

Wall time: 9.01 ms


In [60]:
%%time
top_similar_vectors(all_data_vectors, abstr_vect, 5)

Wall time: 2.24 s


[{'text_id': 3450,
  'Cosine measure': 0.8699420505073937,
  'Manhattan distance': 0.0036475658416748047,
  'Euclidian distance': 0.0002553206129450146},
 {'text_id': 3804,
  'Cosine measure': 0.8692490834094178,
  'Manhattan distance': 0.00359189510345459,
  'Euclidian distance': 0.0002545712075671184},
 {'text_id': 2474,
  'Cosine measure': 0.8674332872512913,
  'Manhattan distance': 0.00356215238571167,
  'Euclidian distance': 0.0002565429403586811},
 {'text_id': 1847,
  'Cosine measure': 0.8605776711345023,
  'Manhattan distance': 0.0037159323692321777,
  'Euclidian distance': 0.0002625589067626343},
 {'text_id': 616,
  'Cosine measure': 0.8586443273757283,
  'Manhattan distance': 0.003716111183166504,
  'Euclidian distance': 0.0002648846106263862}]

In [72]:
print(data.text[3450])

Сегодня мы узнали, что в мире появился первый суперкомпьютер с производительностью свыше 1 exaFLOPS, причём основанный на компонентах AMD. Компания Nvidia решила ответить на это хотя бы информационно. Она опубликовала пресс-релиз, где рассказывается, что ряд ведущих производителей уже используют её Grace CPU Superchip для создания суперкомпьютеров следующего поколения. Тут речь идёт об эксафлопсных вычислениях. Итак, процессоры Grace CPU Superchip и ускорители Grace Hopper уже планируют использовать Atos, Dell Technologies, Gigabyte, HPE, Inspur, Lenovo и Supermicro. Поскольку суперкомпьютеры вступают в эру экcафлопсного искусственного интеллекта, Nvidia объединяется с нашими OEM-партнёрами, чтобы дать возможность исследователям решать масштабные и ранее недоступные задачи. В области климатологии, исследований в области энергетики, освоения космоса, цифровой биологии, квантовых вычислений и многого другого суперчип Grace CPU Superchip и Grace Hopper Superchip составляют основу самой пе

In [71]:
print(abstract_text)

Привет мир, насколько эффективно можно использовать современные технологии искусственного интеллекта и машинного обучения? Сегодня, думаю, мы с этим разберёмся


### Problem
    Even abstract things get good results, it's caused by 'dimensity curse'

## Mos.ru Data testing

In [74]:
mos_ru_data = pd.read_json('data/mos_ru.json')

In [75]:
mos_ru_data.head(3)

id                                              title  \
0  108157073  На Ливенской улице построят дом по программе р...   
1  108162073  Более четырех тысяч человек будут обеспечивать...   
2  108148073  Данные о 43 тысячах квартир в новостройках по ...   

                                           full_text  
0  В районе Южное Бутово по программе реновации п...  
1  Более 4,4 тысячи сотрудников московских служб ...  
2  Данные о 43 тысячах квартир в новостройках вне...

In [77]:
mos_ru_data.shape

(5711, 3)

In [78]:
fake_news = pd.read_json('data/fakes.json')

In [79]:
fake_news.head()

id                                              title  \
0   1  Москва заняла первое место среди европейских г...   
1   2  Москва стала лидером в Европе в рейтинге иннов...   
2   3  Москва заняла первое место в Европе по инновац...   
3   4  Москва заняла первое место в Европе по инновац...   
4   5  Москва стала первой в Европе среди городов с и...   

                                           full_text  
0  В мире Москва занимает третье место, уступая л...  
1  В мире российская столица заняла третье место,...  
2  Москва обошла европейские столицы в рейтинге и...  
3  Исследовательское агентство StartupBlink соста...  
4  Москва заняла первое место среди европейских г...

In [80]:
%%time
model.train(mos_ru_data.full_text)

Wall time: 18min 25s


In [81]:
%%time
mos_ru_vectors = [model.get_text_vect(item) for item in mos_ru_data.full_text]

Wall time: 17min 24s


In [83]:
%%time
fake_vectors = [model.get_text_vect(item) for item in fake_news.full_text]

Wall time: 607 ms


In [113]:
def print_analytics(top_vect_output, all_texts, target_texts, sym_count=400):
    for output, t_text in zip(top_vect_output, target_texts):
        print("Исходный текст: ")
        print()
        print(t_text[:sym_count] + '...')
        print("-----------------------------------------------------------------")
        print("Похожие тексты: ")
        print()
        
        for sim_texts_output in output:
            print(f"Text #{sim_texts_output['text_id']}")
            print(f"Косинусное сходство -> {sim_texts_output['Cosine measure']}")
            print()
            print(all_texts[sim_texts_output['text_id']][:sym_count] + '...')
            print('\n')
            
        print("==================================================================")

In [92]:
similar_texts = [top_similar_vectors(mos_ru_vectors, item, 5) for item in fake_vectors]

In [114]:
print_analytics(similar_texts, mos_ru_data.full_text, fake_news.full_text)

Исходный текст: 

В мире Москва занимает третье место, уступая лишь Нью-Йорку и Сан-Франциско.
Москва признана первой среди европейских городов в рейтинге инноваций,
помогающих в формировании устойчивости коронавирусу. Она опередила Лондон и
Барселону.
Среди мировых мегаполисов российская столица занимает третью строчку —
после Сан-Франциско и Нью-Йорка. Пятерку замыкают Бостон и Лондон. Рейтинг
составило междунаро...
-----------------------------------------------------------------
Похожие тексты: 

Text #3904
Косинусное сходство -> 0.9832089700254216

Москва признана первой среди европейских городов в рейтинге инноваций, помогающих в формировании устойчивости коронавирусу. Она опередила Лондон и Барселону.
Среди мировых мегаполисов российская столица занимает третью строчку — после Сан-Франциско и Нью-Йорка. Пятерку замыкают Бостон и Лондон. Рейтинг составило международное исследовательское агентство StartupBlink.
Добиться высоких показателей М...


Text #3268
Косинусное сходство -> 

*Novec vectors*

In [104]:
%%time
model.vocabulary = vocabulary
mos_ru_vectors = [model.get_text_vect(item) for item in mos_ru_data.full_text]

Wall time: 13min 42s


In [105]:
%%time
fake_navec_vectors = [model.get_text_vect(item) for item in fake_news.full_text]

Wall time: 487 ms


In [106]:
%%time
navec_similar_texts = [top_similar_vectors(mos_ru_vectors, item, 5) for item in fake_navec_vectors]

Wall time: 22.7 s


In [112]:
print_analytics(navec_similar_texts, mos_ru_data.full_text, fake_news.full_text)

Исходный текст: 

В мире Москва занимает третье место, уступая лишь Нью-Йорку и Сан-Франциско.
Москва признана первой среди европейских городов в рейтинге инноваций,
помогающих в формировании устойчивости коронавирусу. Она опередила Лондон и
Барселону.
Среди мировых мегаполисов российская столица занимает третью строчку —
после Сан-Франциско и Нью-Йорка. Пятерку замыкают Бостон и Лондон. Рейтинг
составило междунаро...
-----------------------------------------------------------------
Похожие тексты: 

Косинусное сходство -> 0.9617417825300992

Москва признана первой среди европейских городов в рейтинге инноваций, помогающих в формировании устойчивости коронавирусу. Она опередила Лондон и Барселону.
Среди мировых мегаполисов российская столица занимает третью строчку — после Сан-Франциско и Нью-Йорка. Пятерку замыкают Бостон и Лондон. Рейтинг составило международное исследовательское агентство StartupBlink.
Добиться высоких показателей М...


Косинусное сходство -> 0.9483829430578876

Мо

### 